In [5]:
import time
import chainer
from chainer import cuda
import cupy
import numpy as np
import pickle
import os
import chainer.optimizers as O
from lda2vec_model import LDA2Vec
from lda2vec import utils
from lda2vec import prepare_topics, print_top_words_per_topic, topic_coherence

In [16]:
gpu_ids = [0,1,2,3]


with cuda.Device(gpu_ids[0]):
    x_on_gpu1 = cupy.array([1, 2, 3, 4, 5])

In [17]:
x_cpu = np.ones((5, 4, 3), dtype=np.float32)
x_gpu = cuda.to_gpu(x_cpu, device=0)

In [2]:
id="honeypot_1000"
resultmodelid = "honeypot_1000_2"
doprint=True
n_topics=5
batchsize=4096
power=0.75
pretrained=True
temperature=1.0
n_units=300
gpu_id=0

data_dir = os.getenv('data_dir', '../data/')
fn_vocab = ('{data_dir:s}/vocab_'+id+'.pkl').format(data_dir=data_dir)
fn_corpus = ('{data_dir:s}/corpus_'+id+'.pkl').format(data_dir=data_dir)
fn_flatnd = ('{data_dir:s}/flattened_'+id+'.npy').format(data_dir=data_dir)
fn_docids = ('{data_dir:s}/doc_ids_'+id+'.npy').format(data_dir=data_dir)
fn_vectors = ('{data_dir:s}/vectors_'+id+'.npy').format(data_dir=data_dir)
vocab = pickle.load(open(fn_vocab, 'r'))
corpus = pickle.load(open(fn_corpus, 'r'))
flattened = np.load(fn_flatnd)
doc_ids = np.load(fn_docids)
vectors = np.load(fn_vectors)

In [11]:
n_docs = doc_ids.max() + 1
n_vocab = flattened.max() + 1
words = corpus.word_list(vocab)[:n_vocab]
doc_idx, lengths = np.unique(doc_ids, return_counts=True)
doc_lengths = np.zeros(doc_ids.max() + 1, dtype='int32')
doc_lengths[doc_idx] = lengths
tok_idx, freq = np.unique(flattened, return_counts=True)
term_frequency = np.zeros(n_vocab, dtype='int32')
term_frequency[tok_idx] = freq

model = LDA2Vec(n_documents=n_docs, n_document_topics=n_topics,
    n_units=n_units, n_vocab=n_vocab, counts=term_frequency,
    n_samples=15, power=power, temperature=temperature)

In [128]:
import random
random.seed(1)
np.random.seed(1)

cupy.random.seed(1)
os.environ['CHAINER_SEED'] = '1'

In [12]:
model.to_gpu()
optimizer = O.Adam()
optimizer.setup(model)
clip = chainer.optimizer.GradientClipping(threshold=5.0)
optimizer.add_hook(clip)

losses = []
priors = []
import time
t3 = time.time()
fraction = batchsize * 1.0 / flattened.shape[0]
for epoch in range(200):
    print(epoch)
    t_prepare_topics = time.time()
    data = prepare_topics(cuda.to_cpu(model.mixture.weights.W.data).copy(),
                              cuda.to_cpu(model.mixture.factors.W.data).copy(),
                              cuda.to_cpu(model.sampler.W.data).copy(),
                              words)
    print("Topic Prepare took", time.time()-t_prepare_topics)
    #top_words = print_top_words_per_topic(data)
    
    data['doc_lengths'] = doc_lengths
    data['term_frequency'] = term_frequency
        
    for d, f in utils.chunks(batchsize, doc_ids, flattened):
        #print(len(d), len(f))
        t0 = time.time()
        optimizer.target.cleargrads()
        l = model.fit_partial(d.copy(), f.copy())
        prior = model.prior()
        loss = prior * fraction
        loss.backward()
        optimizer.update()
        msg = ("~~~ USUAL: E:{epoch:05d} L:{loss} "
               "P:{prior:1.3e} R:{rate:1.3e}")

        prior.to_cpu()
        loss.to_cpu()

        t1 = time.time()
        dt = t1 - t0
        rate = batchsize / dt

        logs = dict(loss=float(l), epoch=epoch,
                    prior=float(prior.data), rate=rate)
        #print msg.format(**logs)
            
print(time.time() - t3)

0
context  [  4.97013424e-03  -7.26039230e-04   1.12884841e-03  -3.13333556e-04
  -1.22307707e-03  -8.57400591e-04   7.32837580e-05   7.65835308e-03
  -2.18660990e-03   4.39305697e-03   2.38118204e-03   3.38957272e-03
   6.65027299e-04   6.62287464e-04   1.08724064e-03   3.69119283e-04
   2.85526784e-03   3.61399632e-03   8.82095599e-04   7.02078978e-04
   2.08351901e-03   3.02591268e-03   4.94922837e-03   5.86501649e-03
  -1.75420556e-03   4.64936718e-03   3.63094645e-04  -2.24720500e-03
  -1.45144621e-03  -2.90271896e-03   2.96217413e-03   4.19616047e-03
  -3.80344776e-04   1.18975982e-03  -2.33624852e-03  -1.82070991e-03
  -1.18171098e-03  -3.79404868e-04   6.80364028e-04   3.76290031e-04
   2.94705504e-03   5.17607201e-04   3.32162180e-03   4.06033883e-04
   7.73176085e-04  -1.86561269e-03   1.30992779e-03  -8.26613450e-06
   5.91702701e-04  -3.51221603e-03  -2.38204026e-03  -1.43512196e-04
  -1.41961069e-03  -7.03843834e-04  -1.02051359e-03  -4.26088227e-03
   2.62777740e-03   1.4

2
context  [  4.97013424e-03  -2.39609438e-03  -5.41206449e-04  -2.31286930e-03
  -2.89313169e-03  -2.52745580e-03  -1.92633923e-03   5.98829798e-03
  -2.18660990e-03   2.39233603e-03   1.63704681e-03   3.38957272e-03
  -1.00502768e-03  -8.18479457e-05  -9.13331285e-04  -1.30093587e-03
   8.55469843e-04   3.61399632e-03  -1.11690001e-03   7.02078978e-04
   1.33938401e-03   1.35585805e-03   4.20509279e-03   3.86546971e-03
  -2.49834033e-03   4.64936718e-03   3.63094645e-04  -4.24750429e-03
  -2.19558133e-03  -3.64685454e-03   9.63249360e-04   4.19616047e-03
  -2.37817317e-03  -4.80295275e-04  -3.08038411e-03  -2.56484491e-03
  -3.18036182e-03  -1.12353999e-03  -6.37710327e-05  -3.67845205e-04
   9.49680456e-04   5.17607201e-04   1.65156671e-03  -3.38101294e-04
  -8.96879064e-04  -1.86561269e-03   1.30992779e-03  -7.52401422e-04
  -1.07835210e-03  -3.51221603e-03  -2.38204026e-03  -1.81356724e-03
  -2.16374593e-03  -7.03843834e-04  -1.02051359e-03  -5.93093690e-03
   9.57722426e-04  -5.8

4
context  [  4.38900711e-03  -3.88262165e-03  -1.77301606e-03  -3.71841923e-03
  -4.38766181e-03  -4.22077719e-03  -3.33201210e-03   4.75737639e-03
  -3.60732875e-03   3.92817194e-04  -1.33112771e-04   2.22748425e-03
  -2.23945174e-03  -1.64315524e-03  -2.91070226e-03  -2.24317005e-03
  -7.72698841e-04   2.45190854e-03  -3.09727900e-03   7.02078978e-04
   2.37320201e-05   4.13624162e-04   2.43814522e-03   2.05097580e-03
  -3.54474247e-03   3.48727847e-03  -1.05760945e-03  -6.06778450e-03
  -3.51680536e-03  -4.69325809e-03  -1.03777274e-03   2.77673313e-03
  -4.37435508e-03  -1.96105684e-03  -4.12678765e-03  -4.12612222e-03
  -4.58466727e-03  -2.16994272e-03  -1.62010849e-03  -1.41424814e-03
  -4.52830456e-04   5.17607201e-04   4.18752315e-04  -2.10888311e-03
  -2.37789843e-03  -2.44673993e-03   1.47839077e-04  -2.31499923e-03
  -2.57076183e-03  -4.09334339e-03  -3.80253769e-03  -3.04382807e-03
  -3.93472612e-03  -7.03843834e-04  -2.44097738e-03  -6.87317085e-03
  -5.29464567e-04  -2.5

6
context  [  2.84148124e-03  -5.14636235e-03  -3.44302948e-03  -4.93101589e-03
  -5.44671994e-03  -5.78282773e-03  -4.90241917e-03   3.25684552e-03
  -4.83781891e-03  -1.33926328e-03  -1.73077546e-03   1.40400173e-03
  -3.91069194e-03  -2.74953316e-03  -4.77067474e-03  -3.41584370e-03
  -2.11872091e-03   1.36771123e-03  -4.81430534e-03  -3.13549099e-04
  -1.68123934e-03  -5.27345343e-04   1.00629195e-03   2.72362435e-04
  -4.79212683e-03   1.99660473e-03  -2.81233015e-03  -7.84820132e-03
  -5.06549235e-03  -5.93116926e-03  -2.61342525e-03   1.54827489e-03
  -5.94604341e-03  -3.57600348e-03  -5.37425233e-03  -5.78849344e-03
  -6.16437895e-03  -3.18319490e-03  -2.72296462e-03  -2.15575309e-03
  -1.85194821e-03   5.17607201e-04  -1.08145748e-03  -3.54306167e-03
  -3.82432435e-03  -3.36126308e-03  -9.34343436e-04  -3.80489952e-03
  -3.62831773e-03  -5.00786677e-03  -5.22938371e-03  -4.54998855e-03
  -5.53663261e-03  -1.22596056e-03  -3.86628881e-03  -8.06812756e-03
  -1.97046017e-03  -4.4

context  [ -5.58106462e-03  -5.19706588e-03  -5.60762221e-03  -1.60513981e-03
  -1.14394287e-02  -5.49199758e-03  -6.93126675e-03  -4.02517617e-03
  -8.36213864e-03  -8.01360328e-03  -1.02500785e-02  -2.57297675e-03
  -1.19713191e-02  -8.53479467e-03  -4.78593726e-03  -1.24298164e-03
  -1.13970833e-03   3.03529436e-03  -7.00823078e-03  -9.81292874e-03
  -5.51956519e-03  -6.48502167e-03  -4.96070320e-03  -3.84080457e-03
  -1.31409685e-03  -7.05542415e-03  -6.11381512e-03  -9.53563862e-03
  -6.26580650e-03  -1.09913368e-02  -2.30253488e-03  -4.27862210e-03
  -6.57962169e-03  -9.59613267e-03  -2.60435417e-03  -6.87813945e-03
  -1.63671630e-03  -3.68814846e-03  -5.24019590e-03  -8.66910350e-03
  -9.08555649e-03  -8.43285304e-03  -3.82473483e-03  -4.34486382e-03
  -3.60256224e-03  -1.86100299e-03  -6.50200760e-03  -2.02055601e-03
  -6.41029654e-03  -1.79859586e-02  -1.52721989e-03  -2.26574205e-03
   1.58288330e-03  -3.21161398e-03  -1.21995183e-02  -5.50501887e-03
  -1.17355073e-02  -6.161

...

('Topic Prepare took', 0.08253121376037598)
192
context  [-0.12302878 -0.1395584  -0.12516171 -0.14664072 -0.13000081 -0.14469448
 -0.12468465 -0.13919869 -0.14279659 -0.13609153 -0.13494588 -0.13167804
 -0.14143197 -0.14553073 -0.13653383 -0.14309888 -0.13572171 -0.13432218
 -0.13766283 -0.13204624 -0.13356547 -0.14036375 -0.12864758 -0.12432309
 -0.13650754 -0.12280015 -0.12571545 -0.1492164  -0.13022122 -0.14043367
 -0.13994801 -0.12863594 -0.14880821 -0.14304899 -0.14058776 -0.12247258
 -0.14169411 -0.12652859 -0.1454768  -0.14403743 -0.13601339 -0.13331814
 -0.13113481 -0.12838344 -0.13795222 -0.14126994 -0.13156083 -0.12899126
 -0.13253219 -0.14902    -0.13464625 -0.12806341 -0.13143894 -0.14344929
 -0.13763152 -0.14653136 -0.1405592  -0.1213497  -0.12660319 -0.12958071
 -0.1420864  -0.13521609 -0.1322048  -0.13864051 -0.12912847 -0.14258601
 -0.12232921 -0.14837049 -0.14183183 -0.12586409 -0.13715652 -0.14169036
 -0.1493569  -0.13753368 -0.14552875 -0.14527683 -0.12943299 -0.137

context  [-0.14329816 -0.13944076 -0.13338579 -0.13047236 -0.14218433 -0.1426159
 -0.12416021 -0.12920901 -0.14670345 -0.13107643 -0.13269433 -0.13770966
 -0.12867671 -0.12297022 -0.13591629 -0.12989871 -0.1299766  -0.13390289
 -0.14199929 -0.14110532 -0.13025641 -0.14131993 -0.12637813 -0.14063302
 -0.135263   -0.13974927 -0.12369305 -0.14232826 -0.13584159 -0.13071823
 -0.13601194 -0.13589685 -0.14521739 -0.14850684 -0.13723792 -0.12508595
 -0.13793455 -0.12809545 -0.13510206 -0.13021237 -0.14147909 -0.1419961
 -0.14619294 -0.1388386  -0.1364345  -0.15058605 -0.13237289 -0.13705459
 -0.14113405 -0.14049812 -0.13999358 -0.13385695 -0.14630379 -0.13794094
 -0.13437448 -0.15340616 -0.14236522 -0.12269156 -0.13582303 -0.1271378
 -0.1262777  -0.13969053 -0.13918056 -0.12951481 -0.13649143 -0.14267939
 -0.13255267 -0.13660027 -0.13925956 -0.13963071 -0.14521766 -0.14442223
 -0.14466576 -0.12450768 -0.14174388 -0.13686499 -0.14492251 -0.13740823
 -0.14129077 -0.1273571  -0.14139137 -0.11697

195
context  [-0.12523974 -0.14183185 -0.12765382 -0.14922814 -0.13322954 -0.14686795
 -0.12582275 -0.142023   -0.14530031 -0.13769449 -0.1368233  -0.13340348
 -0.14294538 -0.14836378 -0.1387347  -0.14474325 -0.13808934 -0.1369248
 -0.14031771 -0.13423049 -0.13542107 -0.14308286 -0.1304341  -0.1269812
 -0.13938755 -0.12405954 -0.12812562 -0.15167268 -0.13231075 -0.14320931
 -0.14257729 -0.13098618 -0.15108085 -0.14525691 -0.14278281 -0.12454983
 -0.14410104 -0.12838233 -0.14779025 -0.14617479 -0.13788304 -0.13519844
 -0.13379028 -0.13081527 -0.13990007 -0.14318796 -0.13380879 -0.13093725
 -0.134619   -0.15137765 -0.13645506 -0.12989634 -0.13341144 -0.14576827
 -0.13935311 -0.14870867 -0.1419359  -0.12346077 -0.12942068 -0.13208742
 -0.14409289 -0.13670135 -0.13399987 -0.14090931 -0.13144612 -0.14480907
 -0.12441923 -0.15047818 -0.14345533 -0.12840119 -0.138419   -0.14470221
 -0.15162873 -0.13911562 -0.14829253 -0.14794435 -0.13197587 -0.13875516
 -0.14130147 -0.13720873 -0.13774078 -0.

197
context  [-0.1268913  -0.14350553 -0.1291744  -0.15079884 -0.13512115 -0.14834449
 -0.12668836 -0.14372835 -0.14722425 -0.13887137 -0.13838369 -0.13429171
 -0.14386295 -0.15029001 -0.14025028 -0.14571665 -0.1399366  -0.13869973
 -0.1420864  -0.13557737 -0.13650773 -0.144563   -0.13195585 -0.12860556
 -0.14145069 -0.12510584 -0.12974362 -0.15317561 -0.13388352 -0.14478965
 -0.14393082 -0.13237879 -0.15249108 -0.14656621 -0.1442344  -0.12607424
 -0.1458856  -0.12941612 -0.1491304  -0.14740774 -0.13893153 -0.13663884
 -0.13576926 -0.13245811 -0.14131649 -0.14417532 -0.13530152 -0.13193902
 -0.13569325 -0.15267749 -0.13754182 -0.13116282 -0.13442685 -0.14757836
 -0.14023936 -0.15038297 -0.14264461 -0.12511103 -0.13095725 -0.13337785
 -0.14537416 -0.13794911 -0.13524437 -0.14249107 -0.13299252 -0.14643794
 -0.12564515 -0.15222447 -0.14443037 -0.13028267 -0.13925707 -0.14688073
 -0.15287602 -0.14035808 -0.14996229 -0.14996251 -0.13350023 -0.13991486
 -0.14234799 -0.13855933 -0.13868488 -

199
context  [-0.12838794 -0.14486881 -0.13070472 -0.152362   -0.13679443 -0.15006314
 -0.12768632 -0.14534919 -0.14905711 -0.13997418 -0.1399291  -0.1350152
 -0.14487839 -0.15239306 -0.14188321 -0.14662406 -0.1418418  -0.14050554
 -0.14379577 -0.13719183 -0.13791001 -0.14576864 -0.13360612 -0.1300869
 -0.1434899  -0.1260843  -0.13158937 -0.15477996 -0.13543475 -0.14636061
 -0.14516106 -0.13394907 -0.154044   -0.14778195 -0.14570615 -0.12776674
 -0.14785959 -0.13025819 -0.15074214 -0.14878698 -0.13993031 -0.13793509
 -0.13793454 -0.13379626 -0.14260034 -0.14527594 -0.13711481 -0.1329139
 -0.13683052 -0.15416051 -0.13883699 -0.13248399 -0.13553648 -0.14943054
 -0.14096124 -0.15217431 -0.14349993 -0.12658662 -0.13236831 -0.13483851
 -0.14669235 -0.13937208 -0.13682123 -0.14377947 -0.13439047 -0.14788853
 -0.12721246 -0.15390699 -0.14563996 -0.13237911 -0.14020939 -0.14902957
 -0.15416385 -0.14151433 -0.15145752 -0.15185955 -0.13486557 -0.14098641
 -0.14320041 -0.14015055 -0.13991404 -0.1